In [5]:
import pandas as pd
allseq = pd.read_csv("new_protein_sequences_metadata.tsv", index_col=0)
allseq.head()

aliquot_id\ttranscript_id\tmutated_protein\twildtype_protein\twgs_aliquot_id\tCancer Type\tCancer Stage\tDonor Survival Time\tDonor Age at Diagnosis\tTumour Grade\tFirst Therapy Type\tFirst Therapy Response\tgene_name
8fb9496e-ddb8-11e4-ad8f-5ed8e2d07381\tENST00000...   JP\t2\t1440.0\t67.0\t1\tUnknown\tUnknown\tLIM...                                                                                                                                                                       
26077f8f-9cd2-43c9-8e3e-f4e67afddd35\tENST00000...                                                NaN                                                                                                                                                                       
533707b4-6a23-4bd2-93db-12581927267c\tENST00000...                                                NaN                                                                                                                                                                       
78029317-b987-4292-abfe-fe6a1036c805\tENST00000...                                                NaN                                                                                                                                                                       
bf3c3e52-0191-4714-a7fc-3c9ca9ff3332\tENST00000...                                                NaN

In [7]:
import pandas as pd

# Load the TSV file into a DataFrame
allseq = pd.read_csv("new_protein_sequences_metadata.tsv", sep='\t', index_col=0)

# Extract columns for 'wildtype_protein' and save to a CSV with 'transcript_id' and 'wgs_aliquot_id'
wildtype_protein_df = allseq[['transcript_id', 'wgs_aliquot_id', 'wildtype_protein']]
wildtype_protein_df.to_csv('wildtype_protein_with_ids.csv', index=False)

# Extract columns for 'mutated_protein' and save to a CSV with 'transcript_id' and 'wgs_aliquot_id'
mutated_protein_df = allseq[['transcript_id', 'wgs_aliquot_id', 'mutated_protein']]
mutated_protein_df.to_csv('mutated_protein_with_ids.csv', index=False)

print("CSV files 'wildtype_protein_with_ids.csv' and 'mutated_protein_with_ids.csv' created successfully!")

CSV files 'wildtype_protein_with_ids.csv' and 'mutated_protein_with_ids.csv' created successfully!


In [9]:
wildtype_protein_df = pd.read_csv('wildtype_protein_with_ids.csv')
mutated_protein_df = pd.read_csv('mutated_protein_with_ids.csv')

print(len(wildtype_protein_df))
print(len(mutated_protein_df))
wildtype_protein_unique = wildtype_protein_df.drop_duplicates(subset=['wildtype_protein'])
mutated_protein_unique = mutated_protein_df.drop_duplicates(subset=['mutated_protein'])

# Step 2: Filter based on sequence length <= 3900 for both wildtype and mutated proteins
wildtype_protein_filtered = wildtype_protein_unique[wildtype_protein_unique['wildtype_protein'].str.len() <= 3900]
mutated_protein_filtered = mutated_protein_unique[mutated_protein_unique['mutated_protein'].str.len() <= 3900]

# Save the filtered DataFrames to new CSV files
wildtype_protein_filtered.to_csv('wildtype_protein_filtered.csv', index=False)
mutated_protein_filtered.to_csv('mutated_protein_filtered.csv', index=False)

print("Filtered CSV files 'wildtype_protein_filtered.csv' and 'mutated_protein_filtered.csv' created successfully!")

print(len(wildtype_protein_filtered))
print(len(mutated_protein_filtered))

80840
80840
Filtered CSV files 'wildtype_protein_filtered.csv' and 'mutated_protein_filtered.csv' created successfully!
32838
66126


In [23]:
from esm.models.esm3 import ESM3
from esm.sdk.api import ESMProtein, SamplingConfig
from esm.utils.constants.models import ESM3_OPEN_SMALL
import torch
import pandas as pd
import json
from tqdm import tqdm
from huggingface_hub import login

# Log in to Hugging Face using your token
login()

# Load the CSV file
# print("Loading CSV file...")
df = pd.read_csv('mutated_protein_filtered.csv')

gpu_client = ESM3.from_pretrained(ESM3_OPEN_SMALL, device=torch.device("cuda"))

def get_embedding(sequence):
    print(len(sequence))
    if len(sequence) > 3900:
        raise ValueError(f"Sequence length ({len(sequence)}) exceeds maximum length of 3900")
    torch.cuda.empty_cache()
    protein = ESMProtein(sequence=sequence)
    protein_tensor = gpu_client.encode(protein)
    with torch.no_grad():
        output = gpu_client.forward_and_sample(
            protein_tensor, SamplingConfig(return_mean_embedding=True)
        )
    whole_protein_embedding = output.mean_embedding 
    print(len(whole_protein_embedding))
    embedding_list = whole_protein_embedding.tolist()
    embedding_string = ", ".join(f"{value}" for value in embedding_list)
    return embedding_string




if 'Embedding' not in df.columns:
    df['Embedding'] = None  # Add an empty 'Embedding' column

# Iterate over the rows
embedding_list = []

for _, row in tqdm(df.iterrows(), total=len(df), desc="Processing rows"):
    sequence = row['mutated_protein']
    embedding = row['Embedding']
    if pd.notna(embedding):
        embedding_list.append(embedding)
    else:
        try:
            embedding = get_embedding(sequence)
            embedding_list.append(embedding)
        except Exception as e:
            print(f"Failed to process sequence: {str(e)}")
            embedding_list.append(None)

# Add the Embedding column to the DataFrame
df['Embedding'] = embedding_list


# # Create a list for Embedding
# embedding_list = []

# # Process each row in the DataFrame
# print("Processing sequences...")

# for _, row in tqdm(df.iterrows(), total=len(df), desc="Processing rows"):
#     sequence = row['sequence']
#     embedding = row['Embedding']
#     if embedding == embedding:
#         embedding_list.append(embedding)
#     else:
#         try:
#             embedding = get_embedding(sequence)
#             embedding_list.append(embedding)
#         except Exception as e:
#             print(f"Failed to process sequence: {str(e)}")
#             embedding_list.append(None)

# # Add the Embedding column to the DataFrame
# df['Embedding'] = embedding_list

# Save the updated DataFrame to a new CSV file
output_file = 'tcga_mutated_protein_embeddings.csv'
df.to_csv(output_file, index=False)
print(f"Data with embeddings saved to '{output_file}'")

# Print summary
print(f"Total rows: {len(df)}")
print(f"Successful embeddings: {len([e for e in embedding_list if e is not None])}")
print(f"Failed embeddings: {len([e for e in embedding_list if e is None])}")

/usr/local/lib/python3.10/dist-packages/esm/pretrained.py:68: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state_dict = torch.load(
Processing rows:   0%|          | 2/6612

981
1536
427
1536
794
1536
490


Processing rows:   0%|          | 8/66126 [00:00<49:57, 22.05it/s]  

1536
202
1536
428
1536
536
1536
520
1536
342
1536
300


Processing rows:   0%|          | 14/66126 [00:00<46:19, 23.79it/s]

...

1536
155
1536
120
1536
664
1536
129
1536
162


Processing rows: 100%|█████████▉| 66123/66126 [1:19:35<00:00, 13.13it/s]

1536
2056
1536
314
1536
515


Processing rows: 100%|██████████| 66126/66126 [1:19:35<00:00, 13.85it/s]


1536
143
1536
Data with embeddings saved to 'tcga_mutated_protein_embeddings.csv'
Total rows: 66126
Successful embeddings: 66109
Failed embeddings: 17


In [24]:
df_failed = df[df['Embedding'].isna()]

In [26]:
k=len(df_failed)

In [32]:
sequence_lengths = df_failed['mutated_protein'].str.len()

# Print the length of each sequence
print(sequence_lengths)

1419     3860
2187     3858
2240     3860
4342     3860
15022    3860
23293    3860
24985    3860
32817    3860
33135    3857
33756    3860
39745    3860
45185    3858
48140    3858
49961    3858
53099    3860
53405    3860
55003    3858
Name: mutated_protein, dtype: int64


In [35]:
import pandas as pd

# Load the CSV file into a DataFrame
df = pd.read_csv('tcga_wildtype_protein_embeddings.csv')

# Drop rows where the 'Embedding' column has null (NaN) values
df_cleaned = df.dropna(subset=['Embedding'])

# Save the updated DataFrame back to the same file
df_cleaned.to_csv('tcga_wildtype_protein_embeddings.csv', index=False)

print("Rows with null values in 'Embedding' have been dropped and the cleaned file has been saved.")

Rows with null values in 'Embedding' have been dropped and the cleaned file has been saved.


In [36]:
len(df_cleaned)

32836